# Gold Ore Recovery Model

## Introduction

### Task Statement
I will prepare a prorotype of a machine learning model for Zyfra. Zyfra is a company that develops effieciency solutions for heavy industry. The model will predict the amount of gold recovered from gold ore based on data from Zyfra on gold extration and purification. The model will helpt to optimize the production and eliminate unprofitable parameters.

### Gold Purifying Process
In order to extract gold from ore, the ore is processed through multiple stages in order to obtain the final gold concentrate. The mined ore undergoes primary processing to get the ore mixture or rougher feed. That raw material (rougher feed) then under goes flotation. This flotation process results in a rougher concentrate and rougher tails (product residues with a low concentration of valuable metals). After flotation, the material is sent to a two-stage purification process, delivering the final concentrate and new tails. 

### Data Description
I will be working with 2 datasets, one is the training set that will be used to create the machine learning model and the other will be used as the test dataset. Both of these datasets contain information on different ore mixtures throughout the various stages of the gold purifying process, as well as info on matrials used during the purification process, such as reagent additions, air amounts and float banks. 

### Stages
1. Introduction
2. Data Overview
3. Data Preprocessing
4. Exploratory Data Analysis
5. Feature Preparation
6. Model Creation & Evaluation
7. Conclusion

## Data Overview

In [1]:
# import libraries
import pandas as pd
import numpy as np
import plotly_express as px
import plotly.graph_objects as go
from scipy import stats as st
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.dummy import DummyRegressor
from sklearn.model_selection import cross_val_score
from sklearn.metrics import mean_absolute_error, make_scorer

In [2]:
# load datasets
gold_train = pd.read_csv(
    'gold_recovery_train.csv')
gold_test = pd.read_csv(
    'gold_recovery_test.csv')
gold_full = pd.read_csv(
    'gold_recovery_full.csv')

In [3]:
# general info on train dataset
gold_train.info()
gold_train.sample(5)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16860 entries, 0 to 16859
Data columns (total 87 columns):
 #   Column                                              Non-Null Count  Dtype  
---  ------                                              --------------  -----  
 0   date                                                16860 non-null  object 
 1   final.output.concentrate_ag                         16788 non-null  float64
 2   final.output.concentrate_pb                         16788 non-null  float64
 3   final.output.concentrate_sol                        16490 non-null  float64
 4   final.output.concentrate_au                         16789 non-null  float64
 5   final.output.recovery                               15339 non-null  float64
 6   final.output.tail_ag                                16794 non-null  float64
 7   final.output.tail_pb                                16677 non-null  float64
 8   final.output.tail_sol                               16715 non-null  float64


date  final.output.concentrate_ag  \
8760   2017-05-15 23:59:59                     0.000000   
6373   2017-02-05 12:59:59                     6.841572   
13511  2018-03-31 22:59:59                     0.010000   
1718   2016-03-26 14:00:00                     5.386856   
6528   2017-02-11 23:59:59                     6.015939   

       final.output.concentrate_pb  final.output.concentrate_sol  \
8760                      0.000000                      0.000000   
6373                     11.684240                     14.482600   
13511                     0.010000                      0.010000   
1718                      9.946005                      4.597282   
6528                      8.317966                     15.310543   

       final.output.concentrate_au  final.output.recovery  \
8760                      0.000000                    NaN   
6373                     42.468718              73.412851   
13511                     0.010000             100.000000   
1718                     46.066648              66.567648   
6528                     45.469723              64.173319   

       final.output.tail_ag  final.output.tail_pb  final.output.tail_sol  \
8760               0.000000              0.000000               0.000000   
6373              10.487132              3.963054               7.819264   
13511              0.000000              0.000000               0.000000   
1718              10.406405              1.232452              17.378727   
6528              11.565251              3.876403              11.986831   

       final.output.tail_au  ...  secondary_cleaner.state.floatbank4_a_air  \
8760               0.000000  ...                                  0.000000   
6373               3.228367  ...                                 25.040712   
13511              0.000000  ...                                 22.961458   
1718               2.696734  ...                                 11.925260   
6528               4.371821  ...                                 25.015937   

       secondary_cleaner.state.floatbank4_a_level  \
8760                                  -799.670035   
6373                                  -500.503201   
13511                                 -799.719023   
1718                                  -501.377983   
6528                                  -399.923051   

       secondary_cleaner.state.floatbank4_b_air  \
8760                                   0.000000   
6373                                  23.036541   
13511                                 15.020334   
1718                                  12.003308   
6528                                  23.102569   

       secondary_cleaner.state.floatbank4_b_level  \
8760                                  -799.848966   
6373                                  -500.597974   
13511                                 -562.835371   
1718                                  -500.343774   
6528                                  -399.494149   

       secondary_cleaner.state.floatbank5_a_air  \
8760                                   0.674695   
6373                                  22.984360   
13511                                  0.593582   
1718                                  12.022836   
6528                                  22.999511   

       secondary_cleaner.state.floatbank5_a_level  \
8760                                  -797.711223   
6373                                  -499.520238   
13511                                 -753.200488   
1718                                  -500.170754   
6528                                  -449.655958   

       secondary_cleaner.state.floatbank5_b_air  \
8760                                   0.536756   
6373                                  20.007133   
13511                                  0.613777   
1718                                  10.055137   
6528                                  20.013484   

       secondary_cleaner.state.floatbank5_b_level  \
8760                              

In [4]:
# general info on test dataset
gold_test.info()
gold_test.sample(5)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5856 entries, 0 to 5855
Data columns (total 53 columns):
 #   Column                                      Non-Null Count  Dtype  
---  ------                                      --------------  -----  
 0   date                                        5856 non-null   object 
 1   primary_cleaner.input.sulfate               5554 non-null   float64
 2   primary_cleaner.input.depressant            5572 non-null   float64
 3   primary_cleaner.input.feed_size             5856 non-null   float64
 4   primary_cleaner.input.xanthate              5690 non-null   float64
 5   primary_cleaner.state.floatbank8_a_air      5840 non-null   float64
 6   primary_cleaner.state.floatbank8_a_level    5840 non-null   float64
 7   primary_cleaner.state.floatbank8_b_air      5840 non-null   float64
 8   primary_cleaner.state.floatbank8_b_level    5840 non-null   float64
 9   primary_cleaner.state.floatbank8_c_air      5840 non-null   float64
 10  primary_clea

date  primary_cleaner.input.sulfate  \
4869  2017-11-20 21:59:59                     242.406202   
5401  2017-12-13 01:59:59                     196.457217   
1498  2016-11-02 10:59:59                      94.679020   
4634  2017-11-11 02:59:59                     194.964131   
3963  2017-10-14 03:59:59                     186.216052   

      primary_cleaner.input.depressant  primary_cleaner.input.feed_size  \
4869                          9.901687                             7.56   
5401                          9.993647                             8.55   
1498                          6.979829                             7.27   
4634                         10.050216                             8.47   
3963                          5.448199                             6.97   

      primary_cleaner.input.xanthate  primary_cleaner.state.floatbank8_a_air  \
4869                        2.147017                             1596.303932   
5401                        0.799372                             1553.050105   
1498                        0.698652                             1603.745240   
4634                        1.899766                             1597.797306   
3963                        1.858414                             1397.412053   

      primary_cleaner.state.floatbank8_a_level  \
4869                               -499.755368   
5401                               -500.771079   
1498                               -499.110611   
4634                               -498.243471   
3963                               -500.837883   

      primary_cleaner.state.floatbank8_b_air  \
4869                             1598.859506   
5401                             1550.462546   
1498                             1602.329308   
4634                             1597.049221   
3963                             1403.928605   

      primary_cleaner.state.floatbank8_b_level  \
4869                               -496.669813   
5401                               -498.150696   
1498                               -500.424947   
4634                               -498.743064   
3963                               -500.183177   

      primary_cleaner.state.floatbank8_c_air  ...  \
4869                             1647.999684  ...   
5401                             1549.367274  ...   
1498                             1600.023989  ...   
4634                             1503.489218  ...   
3963                             1402.210319  ...   

      secondary_cleaner.state.floatbank4_a_air  \
4869                                 17.019374   
5401                                 20.023943   
1498                                 14.970912   
4634                                 17.001130   
3963                                 17.991499   

      secondary_cleaner.state.floatbank4_a_level  \
4869                                 -499.809092   
5401                                 -500.082720   
1498                                 -499.296304   
4634                                 -499.989202   
3963                                 -428.467412   

      secondary_cleaner.state.floatbank4_b_air  \
4869                                 14.997259   
5401                                 14.907603   
1498                                 12.978634   
4634                                 14.060091   
3963                                 15.942435   

      secondary_cleaner.state.floatbank4_b_level  \
4869                                 -499.627939   
5401                                 -439.141233   
1498                                 -498.084581   
4634                                 -500.538644   
3963                                 -249.905108   

      secondary_cleaner.state.floatbank5_a_air  \
4869                                 10.965004   
5401                                 10.984554   
1498                                 15.970390   
4634                                 15.025267   
3963                                 13.

In [5]:
# general info on full dataset
gold_full.info()
gold_full.sample(5)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22716 entries, 0 to 22715
Data columns (total 87 columns):
 #   Column                                              Non-Null Count  Dtype  
---  ------                                              --------------  -----  
 0   date                                                22716 non-null  object 
 1   final.output.concentrate_ag                         22627 non-null  float64
 2   final.output.concentrate_pb                         22629 non-null  float64
 3   final.output.concentrate_sol                        22331 non-null  float64
 4   final.output.concentrate_au                         22630 non-null  float64
 5   final.output.recovery                               20753 non-null  float64
 6   final.output.tail_ag                                22633 non-null  float64
 7   final.output.tail_pb                                22516 non-null  float64
 8   final.output.tail_sol                               22445 non-null  float64


date  final.output.concentrate_ag  \
20597  2018-05-22 04:59:59                     5.323930   
18672  2018-03-02 23:59:59                     6.220753   
2094   2016-04-11 06:00:00                     5.203715   
12392  2017-06-14 07:59:59                     4.598055   
1841   2016-03-31 17:00:00                     0.000000   

       final.output.concentrate_pb  final.output.concentrate_sol  \
20597                     9.761469                      7.645611   
18672                     8.764774                      9.498287   
2094                     10.599827                      8.024081   
12392                    11.149784                      9.124488   
1841                      0.000000                      0.000000   

       final.output.concentrate_au  final.output.recovery  \
20597                    43.940517              65.297134   
18672                    44.077925              77.347532   
2094                     45.392616              63.702505   
12392                    44.155471              63.967439   
1841                      0.000000                    NaN   

       final.output.tail_ag  final.output.tail_pb  final.output.tail_sol  \
20597              9.838915              2.377937               8.938469   
18672             12.499237              2.320628              12.392584   
2094               7.977293              2.081138              11.300118   
12392              9.134433              3.370474              10.341056   
1841               0.000000              0.000000               0.000000   

       final.output.tail_au  ...  secondary_cleaner.state.floatbank4_a_air  \
20597              3.232075  ...                                 29.988459   
18672              2.137386  ...                                 23.014906   
2094               2.983094  ...                                 13.986004   
12392              3.272128  ...                                 18.003288   
1841               0.000000  ...                                 11.913709   

       secondary_cleaner.state.floatbank4_a_level  \
20597                                 -500.434027   
18672                                 -502.157273   
2094                                  -746.295758   
12392                                 -500.962977   
1841                                  -481.274050   

       secondary_cleaner.state.floatbank4_b_air  \
20597                                 19.958311   
18672                                 14.974803   
2094                                  14.020475   
12392                                 13.111043   
1841                                  11.929793   

       secondary_cleaner.state.floatbank4_b_level  \
20597                                 -500.321453   
18672                                 -500.057215   
2094                                  -500.458654   
12392                                 -380.208462   
1841                                  -500.988618   

       secondary_cleaner.state.floatbank5_a_air  \
20597                                 18.017807   
18672                                 18.005060   
2094                                  15.041578   
12392                                 17.994273   
1841                                  12.004588   

       secondary_cleaner.state.floatbank5_a_level  \
20597                                 -500.263307   
18672                                 -499.937754   
2094                                  -500.099756   
12392                                 -501.303089   
1841                                  -501.422081   

       secondary_cleaner.state.floatbank5_b_air  \
20597                                 13.989756   
18672                                 11.964634   
2094                                  15.009551   
12392                                 12.982402   
1841                                  10.014890   

       secondary_cleaner.state.floatbank5_b_level  \
20597                             

In [6]:
# check for duplicates in each df
print(gold_train.duplicated().sum())
print(gold_test.duplicated().sum())
print(gold_full.duplicated().sum())

0
0
0


In [7]:
# check for implicit duplicated in each df
print(gold_train.date.duplicated().sum())
print(gold_test.date.duplicated().sum())
print(gold_full.date.duplicated().sum())

0
0
0


There are no duplicate values in any of the datasets, but there are some missing values in each dataset. I will have to look further into these missing values and will have to determine how to deal with them prior to model creation. 

### Check Recovery Calculation

In [8]:
# create function to calculate Recovery
def recovery(df, C, F, T):
    recovery = ((df[C] * (df[F] - df[T])) / (df[F] * (df[C] - df[T]))) * 100
    return recovery

In [9]:
# obtain predicted and actual recovery values
recovery_predicted = recovery(gold_train.dropna(subset=['rougher.output.recovery']),
                              'rougher.output.concentrate_au','rougher.input.feed_au',
                              'rougher.output.tail_au')
recovery_actual = gold_train['rougher.output.recovery'].dropna()
print(recovery_predicted.shape)
print(recovery_actual.shape)

(14287,)
(14287,)


In [10]:
# calculate MAE
mae = mean_absolute_error(recovery_actual,recovery_predicted)
print(f'MeanAbsolute Error: {mae}')

MeanAbsolute Error: 9.210911277458828e-15


With such a small MAE value, we can see that the recovery calculations are correct according to our given formula. 

### Features in each Dataset

In [11]:
# check which columns are in training set but not testing set
extra_features = []
for feature in gold_train.columns:
    if feature not in gold_test.columns:
        extra_features.append(feature)
        print(feature)
extra_features = list(extra_features)

final.output.concentrate_ag
final.output.concentrate_pb
final.output.concentrate_sol
final.output.concentrate_au
final.output.recovery
final.output.tail_ag
final.output.tail_pb
final.output.tail_sol
final.output.tail_au
primary_cleaner.output.concentrate_ag
primary_cleaner.output.concentrate_pb
primary_cleaner.output.concentrate_sol
primary_cleaner.output.concentrate_au
primary_cleaner.output.tail_ag
primary_cleaner.output.tail_pb
primary_cleaner.output.tail_sol
primary_cleaner.output.tail_au
rougher.calculation.sulfate_to_au_concentrate
rougher.calculation.floatbank10_sulfate_to_au_feed
rougher.calculation.floatbank11_sulfate_to_au_feed
rougher.calculation.au_pb_ratio
rougher.output.concentrate_ag
rougher.output.concentrate_pb
rougher.output.concentrate_sol
rougher.output.concentrate_au
rougher.output.recovery
rougher.output.tail_ag
rougher.output.tail_pb
rougher.output.tail_sol
rougher.output.tail_au
secondary_cleaner.output.tail_ag
secondary_cleaner.output.tail_pb
secondary_cleaner.

#### Conclusion
All of the columns that aren't in the test dataset are the result values from each step of the gold purification process. There are also calculations missing such as the rougher calculation gold to lead ration as well as the recovery calculations for both the final output and the rougher output after the floatation process. 

## Data Preprocessing

### Data Types

In [12]:
# change date columns to datetime
gold_full['date'] = pd.to_datetime(gold_full['date'])
gold_train['date'] = pd.to_datetime(gold_train['date'])
gold_test['date'] = pd.to_datetime(gold_test['date'])

### Missing Values in Training Dataset
There are missing values in many of the columns. I do not know which of these columns will be best for my model yet, so I don't want to necessarily drop all of the mising values quite yet. I will go ahead and remove all rows that are missing the values needed for the recovery calculation. Since the MAE between our recovery calculations and the actual recovery values is so low, we can use our calculation to fill those missing values as long as we have all of the other values available to us. I will go ahead and remove any rows with missing values for the columns needed for the recovery calculations. 

In [13]:
# check for columns with missing values
gold_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16860 entries, 0 to 16859
Data columns (total 87 columns):
 #   Column                                              Non-Null Count  Dtype         
---  ------                                              --------------  -----         
 0   date                                                16860 non-null  datetime64[ns]
 1   final.output.concentrate_ag                         16788 non-null  float64       
 2   final.output.concentrate_pb                         16788 non-null  float64       
 3   final.output.concentrate_sol                        16490 non-null  float64       
 4   final.output.concentrate_au                         16789 non-null  float64       
 5   final.output.recovery                               15339 non-null  float64       
 6   final.output.tail_ag                                16794 non-null  float64       
 7   final.output.tail_pb                                16677 non-null  float64       
 8   final.

In [14]:
# drop rows with missing values in rougher & final output recovery columns
gold_train.dropna(subset=['rougher.output.recovery','final.output.recovery'],inplace=True)

In [15]:
# fill missing values using forward fill with limit of 5
for column in gold_train:
    if column != 'date':
        gold_train[column].fillna(method='ffill',inplace=True,limit=5)

/var/folders/bl/tw5qhlsx1yq1d35gh81tcyq80000gn/T/ipykernel_8990/3082169760.py:4: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  gold_train[column].fillna(method='ffill',inplace=True,limit=5)
/var/folders/bl/tw5qhlsx1yq1d35gh81tcyq80000gn/T/ipykernel_8990/3082169760.py:4: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  gold_train[column].fillna(method='ffill',inplace=True,limit=5)


In [16]:
# drop remaining rows with missing values
gold_train.dropna(axis='rows',inplace=True)
gold_train.info()

<class 'pandas.core.frame.DataFrame'>
Index: 12168 entries, 0 to 16859
Data columns (total 87 columns):
 #   Column                                              Non-Null Count  Dtype         
---  ------                                              --------------  -----         
 0   date                                                12168 non-null  datetime64[ns]
 1   final.output.concentrate_ag                         12168 non-null  float64       
 2   final.output.concentrate_pb                         12168 non-null  float64       
 3   final.output.concentrate_sol                        12168 non-null  float64       
 4   final.output.concentrate_au                         12168 non-null  float64       
 5   final.output.recovery                               12168 non-null  float64       
 6   final.output.tail_ag                                12168 non-null  float64       
 7   final.output.tail_pb                                12168 non-null  float64       
 8   final.outpu

### Missing Values in Test Dataset
In order to test the quality of my model with the test dataset, I will need the actual values of the rougher & final output recovery targets. In order to obtain these actual values, I will need to merge those columns from the full dataset. I will use the date column to merget the values correctly. After obtaining these values from the full dataset, I will then remove any rows with any remaining missing values, as I will be unable to run those rows through the ML model. 

In [17]:
# merge target variable columns from full df to test df
gold_test = gold_test.merge(gold_full[['date','rougher.output.recovery','final.output.recovery']],
                           how='left',on='date')
gold_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5856 entries, 0 to 5855
Data columns (total 55 columns):
 #   Column                                      Non-Null Count  Dtype         
---  ------                                      --------------  -----         
 0   date                                        5856 non-null   datetime64[ns]
 1   primary_cleaner.input.sulfate               5554 non-null   float64       
 2   primary_cleaner.input.depressant            5572 non-null   float64       
 3   primary_cleaner.input.feed_size             5856 non-null   float64       
 4   primary_cleaner.input.xanthate              5690 non-null   float64       
 5   primary_cleaner.state.floatbank8_a_air      5840 non-null   float64       
 6   primary_cleaner.state.floatbank8_a_level    5840 non-null   float64       
 7   primary_cleaner.state.floatbank8_b_air      5840 non-null   float64       
 8   primary_cleaner.state.floatbank8_b_level    5840 non-null   float64       
 9   primary_

In [18]:
# remove rows in test dataset with missing values
gold_test.dropna(axis='rows',inplace=True)
gold_test.info()

<class 'pandas.core.frame.DataFrame'>
Index: 5229 entries, 0 to 5855
Data columns (total 55 columns):
 #   Column                                      Non-Null Count  Dtype         
---  ------                                      --------------  -----         
 0   date                                        5229 non-null   datetime64[ns]
 1   primary_cleaner.input.sulfate               5229 non-null   float64       
 2   primary_cleaner.input.depressant            5229 non-null   float64       
 3   primary_cleaner.input.feed_size             5229 non-null   float64       
 4   primary_cleaner.input.xanthate              5229 non-null   float64       
 5   primary_cleaner.state.floatbank8_a_air      5229 non-null   float64       
 6   primary_cleaner.state.floatbank8_a_level    5229 non-null   float64       
 7   primary_cleaner.state.floatbank8_b_air      5229 non-null   float64       
 8   primary_cleaner.state.floatbank8_b_level    5229 non-null   float64       
 9   primary_clean

## Exploratory Data Analysis

### Concentrations of metals during purification process

In [19]:
# group concentrate value columns by type of metal
concentrates_au = ['rougher.input.feed_au','rougher.output.concentrate_au',
                   'primary_cleaner.output.concentrate_au','final.output.concentrate_au']
concentrates_ag = ['rougher.input.feed_ag','rougher.output.concentrate_ag',
                  'primary_cleaner.output.concentrate_ag','final.output.concentrate_ag']
concentrates_pb = ['rougher.input.feed_pb','rougher.output.concentrate_pb',
                  'primary_cleaner.output.concentrate_pb','final.output.concentrate_pb']

In [20]:
# histogram of Au concentrates throughout purification
newnames_au = {'rougher.input.feed_au':'Pre Floatation',
            'rougher.output.concentrate_au':'Post Floatation',
            'primary_cleaner.output.concentrate_au':'Post 1st Cleaner',
            'final.output.concentrate_au':'Final Output'}
hist1 = px.histogram(gold_train,x=concentrates_au,
                     barmode='overlay',title='Au Concentrates Through Purification Process',
                     range_x=[1,55],nbins=100,
                     labels={'variable':'Purification Stage',
                             'value':'Concentrate Value'})
hist1.for_each_trace(lambda t:t.update(name = newnames_au[t.name],
                                       legendgroup = newnames_au[t.name],
                                       hovertemplate=t.hovertemplate.replace(
                                           t.name,newnames_au[t.name]
                                       )))
hist1.show()

In [21]:
# histogram of Ag concentrates throughout purification
newnames_ag = {'rougher.input.feed_ag':'Pre Floatation',
            'rougher.output.concentrate_ag':'Post Floatation',
            'primary_cleaner.output.concentrate_ag':'Post 1st Cleaner',
            'final.output.concentrate_ag':'Final Output'}
hist2 = px.histogram(gold_train,x=concentrates_ag,
                     barmode='overlay',title='Ag Concentrates Through Purification Process',
                     nbins=100,range_x=[0,25],
                     labels={'variable':'Purification Stage',
                             'value':'Concentrate Value'})
hist2.for_each_trace(lambda t:t.update(name = newnames_ag[t.name],
                                       legendgroup = newnames_ag[t.name],
                                       hovertemplate=t.hovertemplate.replace(
                                           t.name,newnames_ag[t.name]
                                       )))
hist2.show()

In [22]:
# histogram of Pb concentrates throughout purification
newnames_pb = {'rougher.input.feed_pb':'Pre Floatation',
            'rougher.output.concentrate_pb':'Post Floatation',
            'primary_cleaner.output.concentrate_pb':'Post 1st Cleaner',
            'final.output.concentrate_pb':'Final Output'}
hist3 = px.histogram(gold_train,x=concentrates_pb,
                     barmode='overlay',title='Pb Concentrates Through Purification Process',
                     nbins=100,range_x=[0,20],
                     labels={'variable':'Purification Stage',
                             'value':'Concentrate Value'})
hist3.for_each_trace(lambda t:t.update(name = newnames_pb[t.name],
                                       legendgroup = newnames_pb[t.name],
                                       hovertemplate=t.hovertemplate.replace(
                                           t.name,newnames_pb[t.name]
                                       )))
hist3.show()

#### Conclusion
Throughout the purification process the gold (Au) concentrates get larger, the other metal concentrates also change throughout the purification process, but in different ways than that of the gold (Au). The lead (Pb) concentrates are the most similar to that of the gold, in that the concentrate value increases throughout the purification process, but in the last 2 stages, the concentrate value doesn't seem to chage. The silver (Ag) concentrates increase after the floatation process, but then begins to decrease with each subsequent step in the purification process.

### Feed Size Distributions

In [23]:
hist4 = go.Figure()
hist4.add_trace(go.Histogram(x=gold_test['rougher.input.feed_size'],
                             name='test data',opacity=0.5,nbinsx=100))
hist4.add_trace(go.Histogram(x=gold_train['rougher.input.feed_size'],
                             name='training data',opacity=0.5,nbinsx=100))
hist4.update_layout(title='Rougher Feed Size Distributions')
hist4.update_xaxes(title='Feed Size')
hist4.update_yaxes(title='Frequency')
hist4.show()

In [24]:
hist5 = go.Figure()
hist5.add_trace(go.Histogram(x=gold_test['primary_cleaner.input.feed_size'],name='testing',opacity=0.5,
                            nbinsx=100))
hist5.add_trace(go.Histogram(x=gold_train['primary_cleaner.input.feed_size'],name='training',opacity=0.5,
                            nbinsx=100))
hist5.update_layout(title='Primary Cleaner Feed Size Distributions',legend_title='Dataset')
hist5.update_xaxes(title='Feed Size')
hist5.update_yaxes(title='Frequency')
hist5.show()

In [25]:
# check  variance equality between rougher feed size distributions
levene_rougher = st.levene(gold_test['rougher.input.feed_size'],
                           gold_train['rougher.input.feed_size'])
print(f'Rougher Levene p-value: {levene_rougher.pvalue}')

Rougher Levene p-value: 2.878997909346244e-08


In [26]:
# check variance equality between primary_cleaner feed size distributions
levene_primary = st.levene(gold_test['primary_cleaner.input.feed_size'],
                         gold_train['primary_cleaner.input.feed_size'])
print(f'Primary Cleaner Levene p-value: {levene_primary.pvalue}')

Primary Cleaner Levene p-value: 0.05143837633319209


In [27]:
# check mean equality between rougher feed size distributions
ttest_rougher = st.ttest_ind(gold_test['rougher.input.feed_size'],
                            gold_train['rougher.input.feed_size'])
print(f'Rougher ttest p-value: {ttest_rougher.pvalue}')

Rougher ttest p-value: 6.1867317273843294e-09


In [28]:
# check mean equality between primary_cleaner feed size distributions
ttest_primary = st.ttest_ind(gold_test['primary_cleaner.input.feed_size'],
                            gold_train['primary_cleaner.input.feed_size'])
print(f'Primary Cleaner ttest p-value: {ttest_primary.pvalue}')

Primary Cleaner ttest p-value: 8.001134678745118e-23


When we look at the histogram it appears that the 2 feed size distributions look to be pretty similar. I performed the Levene test & ttest to check the equality between the mean and variance of the two distributions, and was able to determine that both are not equal. Because of this I will need to remove the significant outliers in the training data in order to create a better quality model. 

### Concentrate Totals at Various Stages

In [29]:
# create df of metal concentrate values at each purification stage
concentrates = pd.concat([gold_train[concentrates_ag],gold_train[concentrates_au],
                         gold_train[concentrates_pb]],axis='columns')
concentrates.info()
concentrates.head()

<class 'pandas.core.frame.DataFrame'>
Index: 12168 entries, 0 to 16859
Data columns (total 12 columns):
 #   Column                                 Non-Null Count  Dtype  
---  ------                                 --------------  -----  
 0   rougher.input.feed_ag                  12168 non-null  float64
 1   rougher.output.concentrate_ag          12168 non-null  float64
 2   primary_cleaner.output.concentrate_ag  12168 non-null  float64
 3   final.output.concentrate_ag            12168 non-null  float64
 4   rougher.input.feed_au                  12168 non-null  float64
 5   rougher.output.concentrate_au          12168 non-null  float64
 6   primary_cleaner.output.concentrate_au  12168 non-null  float64
 7   final.output.concentrate_au            12168 non-null  float64
 8   rougher.input.feed_pb                  12168 non-null  float64
 9   rougher.output.concentrate_pb          12168 non-null  float64
 10  primary_cleaner.output.concentrate_pb  12168 non-null  float64
 11  final.o

rougher.input.feed_ag  rougher.output.concentrate_ag  \
0               6.100378                      11.500771   
1               6.161113                      11.615865   
2               6.116455                      11.695753   
3               6.043309                      11.915047   
4               6.060915                      12.411054   

   primary_cleaner.output.concentrate_ag  final.output.concentrate_ag  \
0                               8.547551                     6.055403   
1                               8.558743                     6.029369   
2                               8.603505                     6.055926   
3                               7.221879                     6.047977   
4                               9.089428                     6.148599   

   rougher.input.feed_au  rougher.output.concentrate_au  \
0               6.486150                      19.793808   
1               6.478583                      20.050975   
2               6.362222                      19.737170   
3               6.118189                      19.320810   
4               5.663707                      19.216101   

   primary_cleaner.output.concentrate_au  final.output.concentrate_au  \
0                              34.174427                    42.192020   
1                              34.118526                    42.701629   
2                              33.969464                    42.657501   
3                              28.260743                    42.689819   
4                              33.044932                    42.774141   

   rougher.input.feed_pb  rougher.output.concentrate_pb  \
0               2.284912                       7.101074   
1               2.266033                       7.278807   
2               2.159622                       7.216833   
3               2.037807                       7.175616   
4               1.786875                       7.240205   

   primary_cleaner.output.concentrate_pb  final.output.concentrate_pb  
0                              10.389648                     9.889648  
1                              10.497069                     9.968944  
2                              10.354494                    10.213995  
3                               8.496563                     9.977019  
4                               9.986786                    10.142511

In [30]:
# create total concentrate amount column for rougher input, rougher output & final output
concentrates['rougher.input.concentrates'] = concentrates['rougher.input.feed_ag'] + concentrates[
    'rougher.input.feed_au'] + concentrates['rougher.input.feed_pb']
concentrates['rougher.output.concentrates'] = concentrates['rougher.output.concentrate_ag'] + concentrates[
    'rougher.output.concentrate_au'] + concentrates['rougher.output.concentrate_pb']
concentrates['final.output.concentrates'] = concentrates['final.output.concentrate_ag'] + concentrates[
    'final.output.concentrate_au'] + concentrates['final.output.concentrate_pb']

# check changes
concentrates.info()

<class 'pandas.core.frame.DataFrame'>
Index: 12168 entries, 0 to 16859
Data columns (total 15 columns):
 #   Column                                 Non-Null Count  Dtype  
---  ------                                 --------------  -----  
 0   rougher.input.feed_ag                  12168 non-null  float64
 1   rougher.output.concentrate_ag          12168 non-null  float64
 2   primary_cleaner.output.concentrate_ag  12168 non-null  float64
 3   final.output.concentrate_ag            12168 non-null  float64
 4   rougher.input.feed_au                  12168 non-null  float64
 5   rougher.output.concentrate_au          12168 non-null  float64
 6   primary_cleaner.output.concentrate_au  12168 non-null  float64
 7   final.output.concentrate_au            12168 non-null  float64
 8   rougher.input.feed_pb                  12168 non-null  float64
 9   rougher.output.concentrate_pb          12168 non-null  float64
 10  primary_cleaner.output.concentrate_pb  12168 non-null  float64
 11  final.o

In [31]:
# plot total concentrate value distributions
newnames = {'rougher.input.concentrates':'Pre Floatation',
            'rougher.output.concentrates':'Post Floatation',
            'final.output.concentrates':'Final Output'}
hist6 = px.histogram(concentrates,x=['rougher.input.concentrates',
                                     'rougher.output.concentrates',
                                     'final.output.concentrates'],
                                     barmode='overlay',labels={'value':
                                                               'Total Concentrate Value'},
                                     title='Total Concentrate Values')
hist6.update_layout(legend_title='Purification Stage')
hist6.for_each_trace(lambda t:t.update(name = newnames[t.name],
                                       legendgroup = newnames[t.name],
                                       hovertemplate=t.hovertemplate.replace(
                                           t.name,newnames[t.name]
                                           )))
hist6.show()

The histograms distributions for each each purification stage do have some significant outliers at or close to zero. Although this is a small amount of outliers, I do think they could negatively impact the model so I will remove these outliers. 

## Feature Preparation

### Remove Outliers from Training Dataset
I will remove all rows with outliers in the rougher input concentrates, rougher output concentrates and final output concentrates columns. 

In [32]:
# determine values for concentrate value outliers
rougher_input_hi = concentrates['rougher.input.concentrates'].quantile(0.99)
rougher_input_lo = concentrates['rougher.input.concentrates'].quantile(0.01)
rougher_output_hi = concentrates['rougher.output.concentrates'].quantile(0.99)
rougher_output_lo = concentrates['rougher.output.concentrates'].quantile(0.01)
final_output_hi = concentrates['final.output.concentrates'].quantile(0.99)
final_output_lo = concentrates['final.output.concentrates'].quantile(0.01)

In [33]:
# create outliers df
outliers = concentrates[(concentrates['rougher.input.concentrates']>rougher_input_hi)|
                        (concentrates['rougher.input.concentrates']<rougher_input_lo)|
                        (concentrates['rougher.output.concentrates']>rougher_output_hi)|
                        (concentrates['rougher.output.concentrates']<rougher_output_lo)|
                        (concentrates['final.output.concentrates']>final_output_hi)|
                        (concentrates['final.output.concentrates']<final_output_lo)]

In [34]:
# remove concentrate value outliers
gold_train = gold_train[~gold_train.index.isin(outliers.index)]

# check changes
gold_train.info()

<class 'pandas.core.frame.DataFrame'>
Index: 11581 entries, 0 to 16859
Data columns (total 87 columns):
 #   Column                                              Non-Null Count  Dtype         
---  ------                                              --------------  -----         
 0   date                                                11581 non-null  datetime64[ns]
 1   final.output.concentrate_ag                         11581 non-null  float64       
 2   final.output.concentrate_pb                         11581 non-null  float64       
 3   final.output.concentrate_sol                        11581 non-null  float64       
 4   final.output.concentrate_au                         11581 non-null  float64       
 5   final.output.recovery                               11581 non-null  float64       
 6   final.output.tail_ag                                11581 non-null  float64       
 7   final.output.tail_pb                                11581 non-null  float64       
 8   final.outpu

### Define Features (X) & Targets (y)

In [35]:
# define the features & targets for the training dataset
target_gold_train = gold_train[['rougher.output.recovery',
                                      'final.output.recovery']]
features_gold_train = gold_train.drop(extra_features,axis=1)
features_gold_train = features_gold_train.drop(['date'],axis=1)

In [36]:
# define the features for the testing dataset
target_gold_test = gold_test[['rougher.output.recovery','final.output.recovery']]
features_gold_test = gold_test.drop(['date','rougher.output.recovery','final.output.recovery'],axis=1)

In [37]:
# changing features & targets to array
y_train = target_gold_train.values
y_test = target_gold_test.values
X_train = features_gold_train.values
X_test = features_gold_test.values

## Model Creation & Evaluation

### sMAPE Calculation
In order to judge the quality of the machine learning model, I will be using the symmetric Mean Absolute Percentage Error. I will create a function that will calculate this score for the model. 

In [38]:
# create function to calculate sMAPE
def smape(y_true,y_pred):
    smape = (1/len(y_true)) * sum(abs(y_pred-y_true) / ((abs(y_true)+abs(y_pred)) / 2) * 100)
    return smape

In [39]:
# create function to calculate FINAL sMAPE
def final_smape(y_true,y_pred):
    predicted_rough,predicted_final = y_pred[:,0],y_pred[:,1]
    true_rough,true_final = y_true[:,0],y_true[:,1]
    final_smape = (0.25*(smape(true_rough,predicted_rough)))+(
        0.75*(smape(true_final,predicted_final)))
    return final_smape

In [40]:
# setting scorer for cross validation
smape_score = make_scorer(final_smape)

### Model Training

In [41]:
# creating random state variable
random_state = 12345

In [42]:
# create, train & evaluate Linear Regression model using cross validation
model_lr = LinearRegression()
model_lr.fit(X_train,y_train)
scores_lr = cross_val_score(model_lr,X_train,y_train,cv=5,scoring=smape_score)
print(f'Linear Model Mean sMAPE: {np.mean(scores_lr)}')

Linear Model Mean sMAPE: 10.755836107420322


In [43]:
# train & evaluate Decision Tree Regressor model with various max depths
for depth in range(1,6):
    model = DecisionTreeRegressor(random_state=random_state,max_depth=depth)
    model.fit(X_train,y_train)
    scores = cross_val_score(model,X_train,y_train,cv=5,scoring=smape_score)
    print(f'Decision Tree Regressor Depth: {depth}')
    print(f'Decision Tree Regressor Model Mean sMAPE: {np.nanmean(scores)}')

Decision Tree Regressor Depth: 1
Decision Tree Regressor Model Mean sMAPE: 9.80008783516601
Decision Tree Regressor Depth: 2
Decision Tree Regressor Model Mean sMAPE: 9.566278061516162
Decision Tree Regressor Depth: 3
Decision Tree Regressor Model Mean sMAPE: 9.533368135228594
Decision Tree Regressor Depth: 4
Decision Tree Regressor Model Mean sMAPE: 9.897778856905333


/var/folders/bl/tw5qhlsx1yq1d35gh81tcyq80000gn/T/ipykernel_8990/3909373608.py:3: RuntimeWarning:

invalid value encountered in divide



Decision Tree Regressor Depth: 5
Decision Tree Regressor Model Mean sMAPE: 9.274376728738961


In [44]:
# create, train & evaluate Random Forest Regressor using cross validation
for est in range(10,51,10):
    model = RandomForestRegressor(random_state=random_state,n_estimators=est,max_depth=5)
    model.fit(X_train,y_train)
    scores = cross_val_score(model,X_train,y_train,cv=5,scoring=smape_score)
    print(f'Random Forest Regressor N-est: {est}')
    print(f'Random Forest Regressor Model Mean sMAPE: {np.nanmean(scores)}')

Random Forest Regressor N-est: 10
Random Forest Regressor Model Mean sMAPE: 9.262243605085413
Random Forest Regressor N-est: 20
Random Forest Regressor Model Mean sMAPE: 9.158328016829174
Random Forest Regressor N-est: 30
Random Forest Regressor Model Mean sMAPE: 9.205060756498026
Random Forest Regressor N-est: 40
Random Forest Regressor Model Mean sMAPE: 9.228821056530649
Random Forest Regressor N-est: 50
Random Forest Regressor Model Mean sMAPE: 9.251393720835692


The best model is the Random Forest Regressor with 20 n_estimators & a max depth of 5. I will use these parameters for my final model.

### Using Final Model on Test Dataset

In [45]:
# creating Final Random Forest Regressor model with best parameters
model_rfr = RandomForestRegressor(random_state=random_state,n_estimators=20,max_depth=5)
model_rfr.fit(X_train,y_train)

RandomForestRegressor(max_depth=5, n_estimators=20, random_state=12345)

In [46]:
# use model to predict target values for test dataset
y_pred_test = model_rfr.predict(X_test)

In [47]:
# mean final sMAPE of model with test datset
test_final_smape = final_smape(y_test,y_pred_test)
print(f'Mean Final sMAPE: {test_final_smape}')

Mean Final sMAPE: 9.202909972295167


The final symmetrical mean absolute percentage error is only 9.19% & is very similar to the sMAPE of the training dataset. 

In [48]:
# create, train, test & evaluate DummyRegressor constant model based on mean values
dm = DummyRegressor(strategy='mean').fit(X_train, y_train)
y_pred_mean = dm.predict(X_test)
print(f'Mean Final sMAPE of mean constant model: {final_smape(y_test,y_pred_mean)}')

Mean Final sMAPE of mean constant model: 9.773426625268932


In [49]:
# create, train, test & evaluate DummyRegressor constant model based on median values
dm = DummyRegressor(strategy='median').fit(X_train, y_train)
y_pred_median = dm.predict(X_test)
print(f'Mean Final sMAPE of median constant model: {final_smape(y_test,y_pred_median)}')

Mean Final sMAPE of median constant model: 9.212148616820414


I also evaluated two constant models, one based on the target mean values and the other based on the target median values. The final model has a smaller sMAPE than both of the constant models so this is another indicator that the final model does a good job in predicting the recovery values.

## Final Conclusion
The final sMAPE of the model based on the testing dataset is low enough that I would say that the model is a good predictor of the recovery values of the gold purification process. 